In [1]:
# 분석 환경 모듈
import numpy as np
import pandas as pd
import psycopg2 as pg
import time
import matplotlib
import matplotlib.pyplot as plt
from matplotlib import style

# 데이터 분석 모듈
from CoolProp.CoolProp import PropsSI
from sklearn.preprocessing import MinMaxScaler, QuantileTransformer, PolynomialFeatures
from sklearn.metrics import mean_absolute_error, mean_squared_error
from sklearn.linear_model import LinearRegression
from scipy.integrate import ode

# 내가 만든 모듈 임포트
from Model import *
from PhysicalProperty import *
from StructuredQuery import *
from Numeric import *

style.use('seaborn-talk')
krfont = {'family':'Times New Roman', 'weight':'bold', 'size':10}
matplotlib.rc('font', **krfont)
matplotlib.rcParams['axes.unicode_minus'] = False

In [2]:
# 클래스 정의 및  인스턴스 생성
pro = PhysicalProperty()
mod = ModelOSV()
sql = StructuredQuery()

Property_OSV is successfully started.
Model_OSV is successfully started.
Construct connection string and update
SQL_OSV is successfully started.


In [8]:
"""
# CHF 데이터베이스 연결
load_chf_query = "SELECT * FROM rawdata_chf_tb"
chf_tb = sql.read_sql(load_chf_query, db_engine)
"""

chf_tb = pd.read_excel('sample.xlsx')

no       run    yy             source geo  flow refri  hs      p  \
0      1         1  1981  Green and Stevens   C     1   R12   1   9.31   
1      2         5  1981  Green and Stevens   C     1   R12   1   9.28   
2      3         9  1981  Green and Stevens   C     1   R12   1   9.30   
3      4        13  1981  Green and Stevens   C     1   R12   1   9.28   
4      5        17  1981  Green and Stevens   C     1   R12   1   9.26   
..   ...       ...   ...                ...  ..   ...   ...  ..    ...   
716  717  18027602  1980  Stevens and Miles   C     1   R12   1  10.42   
717  718  18027603  1980  Stevens and Miles   C     1   R12   1  10.43   
718  719  18027604  1980  Stevens and Miles   C     1   R12   1  10.43   
719  720  18027605  1980  Stevens and Miles   C     1   R12   1  10.43   
720  721  18027606  1980  Stevens and Miles   C     1   R12   1  10.43   

         doi      dio       dh    lh  hsur       g  ti        q     xe  
0    0.01798  0.01676  0.01676  2.87     1   666.0 NaN  0.09575  0.583  
1    0.01798  0.01676  0.01676  2.87     1   682.0 NaN  0.08930  0.575  
2    0.01798  0.01676  0.01676  2.87     1   684.0 NaN  0.08237  0.624  
3    0.01798  0.01676  0.01676  2.87     1   611.0 NaN  0.09399  0.635  
4    0.01798  0.01676  0.01676  2.87     1   616.0 NaN  0.08675  0.627  
..       ...      ...      ...   ...   ...     ...  ..      ...    ...  
716  0.01638  0.01534  0.01534  2.85     1  1993.0 NaN  0.12410  0.242  
717  0.01638  0.01534  0.01534  2.85     1  1987.0 NaN  0.11370  0.240  
718  0.01638  0.01534  0.01534  2.85     1  1987.0 NaN  0.11900  0.255  
719  0.01638  0.01534  0.01534  2.85     1  1998.0 NaN  0.10460  0.278  
720  0.01638  0.01534  0.01534  2.85     1  1996.0 NaN  0.11000  0.293  

[721 rows x 18 columns]

In [9]:
# Rawdata에서 Physical property 추가 (for water)
chf_tb['pcrit'] = round(chf_tb[['refri']].apply(lambda x: PropsSI(x[0],'pcrit') * 10**-5, axis=1),6) # [bar]
chf_tb['tsat'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('T', 'P', x[0] * 1e5, 'Q', 0, x[1]), axis=1),6) # [K]
chf_tb['kf'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('L', 'P', x[0] * 1e5, 'Q', 0, x[1]), axis=1),6) # [W/mK]
chf_tb['kv'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('L', 'P', x[0] * 1e5, 'Q', 1, x[1]), axis=1),6) # [W/mK]
chf_tb['muf'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('V', 'P', x[0] * 1e5, 'Q', 1, x[1]), axis=1),12) #  [Pa s]
chf_tb['muv'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('V', 'P', x[0] * 1e5, 'Q', 1, x[1]), axis=1),12) # [Pa s]
chf_tb['hfo'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('H', 'P', x[0] * 1e5, 'Q', 0, x[1]), axis=1),6) # [J/kgK]
chf_tb['hgo'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('H', 'P', x[0] * 1e5, 'Q', 1, x[1]), axis=1),6) #[J/kgK]
chf_tb['lam'] = round(chf_tb['hgo'] - chf_tb['hfo'],6) # [J/kgK]
chf_tb['rhof'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('D', 'P', x[0] * 1e5, 'Q', 0, x[1]), axis=1),6) #[kg/m3]
chf_tb['rhov'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('D', 'P', x[0] * 1e5, 'Q', 1, x[1]), axis=1),6) # [kg/m3]
chf_tb['v'] = round(chf_tb['g'] / chf_tb['rhof'],6) # [m/s]
chf_tb['cpf'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('C', 'P', x[0] * 1e5, 'Q', 0, x[1]), axis=1),6) # [J/kgK]
chf_tb['cpv'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('C', 'P', x[0] * 1e5, 'Q', 1, x[1]), axis=1),6) # [J/kgK]
chf_tb['sigma'] = round(chf_tb[['p', 'refri']].apply(lambda x: PropsSI('I', 'P', x[0] * 1e5, 'Q', 0, x[1]), axis=1),6) # [N/m]
#chf_tb['ti'] = round(chf_tb['tsat'] - chf_tb['dtin'] - 273.15,6) # [K]
# Ti 계산

chf_tb['dtin'] = round(chf_tb[['geo', 'xe', 'q', 'cpf', 'lam', 'lh', 'g', 'dh', 'tsat']].apply(lambda x: pro.calDTin(x[0], x[1], x[2], x[3], x[4], x[5], x[6], x[7], x[8]), axis = 1), 6)


In [12]:

# Rawdata에서 Dimensionless number 추가
chf_tb['xi'] = round(chf_tb[['cpf', 'dtin', 'lam']].apply(lambda x: pro.calXi(x[0], x[1], x[2]), axis = 1),6)
chf_tb['xout'] = round(chf_tb[['q', 'doi', 'dio', 'geo', 'hsur', 'g', 'cpf', 'lam', 'dtin', 'lh']].apply(lambda x: pro.calXout(x[0], x[1], x[2], x[3], x[4], x[5], x[6], x[7], x[8], x[9]), axis=1),6)
chf_tb['de'] = round(chf_tb[['doi', 'dio', 'geo', 'hsur', 'dh']].apply(lambda x: pro.calDe(x[0], x[1], x[2], x[3], x[4]), axis=1),6)
chf_tb['pe'] = round(chf_tb[['dh', 'g', 'cpf', 'kf']].apply(lambda x: pro.calPe(x[0], x[1], x[2], x[3]), axis=1),6)
chf_tb['re'] = round(chf_tb[['g', 'dh', 'muf']].apply(lambda x: pro.calRe(x[0], x[1], x[2]), axis=1),6)
chf_tb['we'] = round(chf_tb[['rhof', 'v', 'dh', 'sigma']].apply(lambda x: pro.calWe(x[0], x[1], x[2], x[3]), axis=1),6)
chf_tb['bd'] = round(chf_tb[['rhof', 'rhov', 'dh', 'sigma']].apply(lambda x: pro.calBd(x[0], x[1], x[2], x[3]), axis=1),6)
chf_tb['bo'] = round(chf_tb[['q', 'lam', 'g']].apply(lambda x: pro.calBo(x[0], x[1], x[2]), axis = 1),6)
chf_tb['ga'] = round(chf_tb[['rhof', 'dh', 'muf']].apply(lambda x: pro.calGa(x[0], x[1], x[2]), axis=1),6)
chf_tb['gz'] = round(chf_tb[['g', 'cpf', 'kf', 'dh']].apply(lambda x: pro.calGz(x[0], x[1], x[2], x[3]), axis=1),6)
chf_tb['z'] = round(chf_tb[['muf', 'rhof', 'dh', 'sigma']].apply(lambda x: pro.calZ(x[0], x[1], x[2], x[3]), axis=1),6)
chf_tb['fr'] = round(chf_tb[['v', 'dh']].apply(lambda x: pro.calFr(x[0], x[1]), axis=1),6)
chf_tb['ca'] = round(chf_tb[['muf', 'v', 'sigma', 'rhof']].apply(lambda x: pro.calCa(x[0], x[1], x[2], x[3]), axis=1),6)
chf_tb['pr'] = round(chf_tb[['cpf', 'muf', 'kf']].apply(lambda x: pro.calPr(x[0], x[1], x[2]), axis=1),6)

print("chf_tb에 Physical property 계산 완료")

chf_tb에 Physical property 계산 완료


In [14]:
# OSV, CHF 설정 모델 삽입 문구
print('chf correlation을 선택하시오: ')
print('(1) Saha and Zuber  (2) Modified Saha and Zuber  (3) Unal')
print('(4) Levy                         (5) Bowring                                    (6) Jeong')
m_idx = int(input('-----너의 선택은? : '))

chf correlation을 선택하시오: 
(1) Saha and Zuber  (2) Modified Saha and Zuber  (3) Unal
(4) Levy                         (5) Bowring                                    (6) Jeong
-----너의 선택은? : 1


In [16]:
# Xt 초기값 계산하는 알고리즘
"""
res_tb: chf_tb (rawdata table)에서 뽑아낸 결과만 저장하는 테이블

"""
# 결과테이블 새로 생성
res_tb = chf_tb

# def sub_xt_return(p, pcrit, dh, g, lam, m_idx):
if m_idx == 1:
    for i, row in res_tb.iterrows():
        res_tb.loc[i, 'dt_sz'], res_tb.loc[i, 'x_sz'] = mod.calSahaZuber(res_tb.loc[i, 'q'], res_tb.loc[i, 'rhof'], res_tb.loc[i, 'dh'], res_tb.loc[i, 'g'],
                                            res_tb.loc[i, 'cpf'], res_tb.loc[i, 'kf'], res_tb.loc[i, 'pe'], res_tb.loc[i, 'lam'])
        res_tb.loc[i,'st_cal'] = res_tb.loc[i,'q']* 10 ** 6 / (res_tb.loc[i,'g'] * res_tb.loc[i,'cpf'] * res_tb.loc[i,'dt_sz'])
    print("Saha and Zuber correlation에 대한 St, Xosv 계산이 모두 끝났습니다.")
elif m_idx == 2:
    for i, row in res_tb.iterrows():
        res_tb.loc[i, 'dt_psz'], res_tb.loc[i, 'x_psz'] = mod.calParkSahaZuber(res_tb.loc[i, 'q'], res_tb.loc[i, 'rhof'], res_tb.loc[i, 'dh'], res_tb.loc[i, 'g'],
                                            res_tb.loc[i, 'cpf'], res_tb.loc[i, 'kf'], res_tb.loc[i, 'pe'], res_tb.loc[i, 'lam'])
        res_tb.loc[i,'st_cal'] = res_tb.loc[i,'q'] * 10 ** 6 / (res_tb.loc[i,'g'] * res_tb.loc[i,'cpf'] * res_tb.loc[i,'dt_psz'])
    print("Park, Saha and Zuber correlation에 대한 St, Xosv 계산이 모두 끝났습니다.")
elif m_idx == 3:
    for i, row in res_tb.iterrows():
        res_tb.loc[i, 'dt_unal'], res_tb.loc[i, 'x_unal'] = mod.calUnal(res_tb.loc[i, 'q'], res_tb.loc[i, 'pr'], res_tb.loc[i, 'dh'], res_tb.loc[i, 'v'],
                                            res_tb.loc[i, 'cpf'], res_tb.loc[i, 'kf'], res_tb.loc[i, 're'], res_tb.loc[i, 'refri'], res_tb.loc[i, 'lam'])
        res_tb.loc[i,'st_cal'] = res_tb.loc[i,'q'] * 10 ** 6 / (res_tb.loc[i,'g'] * res_tb.loc[i,'cpf'] * res_tb.loc[i,'dt_unal'])
    print("Unal correlation에 대한 St, Xosv 계산이 모두 끝났습니다.")
elif m_idx == 4:
    for i, row in res_tb.iterrows():
        res_tb.loc[i, 'dt_levy'], res_tb.loc[i, 'x_levy'] = mod.calLevy(res_tb.loc[i, 'sigma'], res_tb.loc[i, 'dh'], res_tb.loc[i, 'rhof'], res_tb.loc[i, 'muf'],
                                            res_tb.loc[i, 'kf'], res_tb.loc[i, 're'], res_tb.loc[i, 'pr'], res_tb.loc[i, 'cpf'],
                                            res_tb.loc[i, 'g'], res_tb.loc[i, 'q'], res_tb.loc[i, 'lam'], res_tb.loc[i, 'v'])
        res_tb.loc[i,'st_cal'] = res_tb.loc[i,'q']* 10 ** 6 / (res_tb.loc[i,'g'] * res_tb.loc[i,'cpf'] * res_tb.loc[i,'dt_levy'])
    print("Levy Model에 대한 St, Xosv 계산이 모두 끝났습니다.")
elif m_idx == 5:
    for i, row in res_tb.iterrows():
        res_tb.loc[i, 'dt_bowr'], res_tb.loc[i, 'x_bowr'] = mod.calBowring(res_tb.loc[i, 'p'], res_tb.loc[i, 'q'], res_tb.loc[i, 'v'], res_tb.loc[i, 'lam'],
                                                res_tb.loc[i, 'cpf'])
        res_tb.loc[i,'st_cal'] = res_tb.loc[i,'q'] * 10 ** 6 / (res_tb.loc[i,'g'] * res_tb.loc[i,'cpf'] * res_tb.loc[i,'dt_bowr'])
    print("Bowring correlation에 대한 St, Xosv 계산이 모두 끝났습니다.")
else:
    for i, row in res_tb.iterrows():
        res_tb.loc[i, 'dt_js'], res_tb.loc[i, 'x_js'] = mod.calJeong(res_tb.loc[i, 'q'], res_tb.loc[i, 'rhof'], res_tb.loc[i, 'dh'], res_tb.loc[i, 'v'],
                                        res_tb.loc[i, 'cpf'], res_tb.loc[i, 'kf'], res_tb.loc[i, 'pe'], res_tb.loc[i, 'lam'], res_tb.loc[i,'pr'], res_tb.loc[i, 'we'])
        res_tb.loc[i,'st_cal'] = res_tb.loc[i,'q'] * 10 ** 6 / (res_tb.loc[i,'g'] * res_tb.loc[i,'cpf'] * res_tb.loc[i,'dt_js'])
    print("Jeong and Shim correlation에 대한 St, Xosv 계산이 모두 끝났습니다.")    

    # Boundary conditoin설정
"""
- 국부조건 가설을 사용한 CHF를 계산하는 과정
dXt       | h_b - h_l,sat   |
--- =  |----------- |*Xe
dXe      |         \lambda |
"""
# 시간기록 시작 (나중에 여기에 로그도 남겨야함)
startTime = time.time()

# Rate eqn. 설정
def dif(X, Xt):
    global nparam_xosv
    dXt=1+(Xt-X)/(nparam_xosv*(1-Xt));
    return dXt

# Validation set와  error table 만드는 작업 진행
val_chf_tb = res_tb[['source','q','xi','xe','xout']]
val_chf_err_tb = res_tb[['source','q', 'xi','xe','xout']]

try:
    for i, row in val_chf_tb.iterrows():
        # alpha와 gamma 계산
        # 나중에 CHF 모델 선택도 가능하게 추가
        val_chf_tb.loc[i,'alpha'] = 1.669 - 6.544 * ((res_tb.loc[i,'p']/res_tb.loc[i,'pcrit'])-0.448)**2
        val_chf_tb.loc[i,'gamma'] = 0.06523 + (0.1045 / np.sqrt(2* np.pi*(np.log(res_tb.loc[i,'p']/res_tb.loc[i,'pcrit']))**2))* np.exp(-5.413*((np.log(res_tb.loc[i,'p']/res_tb.loc[i,'pcrit'])+0.4537)**2/(np.log(res_tb.loc[i,'p']/res_tb.loc[i,'pcrit']))**2))
        
        # 앞서 계산한 OSV 상관식으로 계산한 st이 삽입된 xosv_cal 계산
        val_chf_tb.loc[i,'xosv_cal'] = round(-(res_tb.loc[i,'q'] * 10**6)/ (res_tb.loc[i,'st_cal'] * res_tb.loc[i,'g'] * res_tb.loc[i,'lam']),6)
        
        # Xt 초기값 계산 (ODE_45)
        nparam_xosv = val_chf_tb.loc[i,'xosv_cal']
        xsol, ysol = rk_ode45(dif,res_tb.loc[i, 'xi'],[val_chf_tb.loc[i,'xosv_cal'],res_tb.loc[i,'xe']],0.0001)
        val_chf_tb.loc[i,'xt_ini'] = round(ysol[-1],6)
        
        if val_chf_tb.loc[i, 'xt_ini'] < 0:
            val_chf_tb.loc[i,'xt_cal'] = 0
        else:
            val_chf_tb.loc[i,'xt_cal'] = round(ysol[-1],6)
        
        cnt = 1
        while 1:
            """
            differential rate eqn.을 돌려보니, xe = xt
            """
            # CHF heat flux를 계산 (Deng 식)
            val_chf_tb.loc[i,'term_deng'] = round(np.sqrt(res_tb.loc[i,'g']*val_chf_tb.loc[i,'xt_cal']*(1+val_chf_tb.loc[i,'xt_cal']**2)**3),6)
            val_chf_tb.loc[i,'q_cal'] = round((val_chf_tb.loc[i,'alpha']/np.sqrt(res_tb.loc[i,'dh']))*np.exp(-val_chf_tb.loc[i,'gamma']*val_chf_tb.loc[i,'term_deng']),6)
            print('heat flux of calculation is {}'.format(val_chf_tb.loc[i, 'q_cal']))
            
            # 오류값 계산 (나중에 바꿔줄 필요 있음)
            val_chf_tb.loc[i, 'q_err'] = round((val_chf_tb.loc[i,'q_cal'] - res_tb.loc[i,'q']) / res_tb.loc[i,'q'],6)
            
            # Error
            # print('error is {}'.format(err))
            
            # 조건 판별 (break 또는 증감)
            try:
                cnt = cnt + 1               
                print('{}번째 시도에서 xt_cal은 {}입니다. '.format(cnt, val_chf_tb.loc[i,'xt_cal']))
                
                if cnt >= 100:
                    raise Exception('divergence error')
                
                if  np.abs(val_chf_tb.loc[i, 'q_err']) < 0.05:
                    print('{}th iteration is converged., xt_cal is {} and error of heat flux is {}.'.format(i, val_chf_tb.loc[i,'xt_cal'], val_chf_tb.loc[i,'q_err']))
                    val_chf_err_tb.loc[i,'idx_err'] = 'Converged'
                    break
                else:
                    if val_chf_tb.loc[i, 'q_err'] > 0:
                        val_chf_tb.loc[i,'xt_cal'] = val_chf_tb.loc[i,'xt_cal'] + 0.01
                        continue
                    #elif val_chf_tb.loc[i,'xt_cal'] > 1:
                    #    val_chf_tb.loc[i,'xt_cal'] = val_chf_tb.loc[i,'xt_cal'] / 2
                    #    continue
                    else:
                        val_chf_tb.loc[i,'xt_cal'] = val_chf_tb.loc[i,'xt_cal'] - 0.01
                        continue
                
            except Exception as e:
                print('{}th iteration is diverged.'.format(i))
                val_chf_err_tb.loc[i,'idx_err'] = 'Diverged'
                break
                                                                                                    
except Exception as e:
    print('The index {} is error occured.'.format(e))
    print(e)
finally:
    print("{} th process is succees!".format(i))

endTime = round(time.time() - startTime,4)
print('전체 시뮬레이션 시간은 {} 모델에 대해 데이터 개수는 {}, 총 걸린 시간은 {} ms입니다.'.format(m_idx, len(chf_tb), endTime)


Saha and Zuber correlation에 대한 St, Xosv 계산이 모두 끝났습니다.
heat flux of calculation is 1.3377069550764642
2번째 시도에서 xt_cal은 0.5814788615412663입니다. 
heat flux of calculation is 1.2791330638562355
3번째 시도에서 xt_cal은 0.5914788615412663입니다. 
heat flux of calculation is 1.2220216174967193
4번째 시도에서 xt_cal은 0.6014788615412663입니다. 
heat flux of calculation is 1.1663865479733504
5번째 시도에서 xt_cal은 0.6114788615412663입니다. 
heat flux of calculation is 1.1122401666772845
6번째 시도에서 xt_cal은 0.6214788615412663입니다. 
heat flux of calculation is 1.0595930361075343
7번째 시도에서 xt_cal은 0.6314788615412663입니다. 
heat flux of calculation is 1.0084538548169981
8번째 시도에서 xt_cal은 0.6414788615412663입니다. 
heat flux of calculation is 0.9588293558092605
9번째 시도에서 xt_cal은 0.6514788615412663입니다. 
heat flux of calculation is 0.9107242185584216
10번째 시도에서 xt_cal은 0.6614788615412663입니다. 
heat flux of calculation is 0.8641409947906603
11번째 시도에서 xt_cal은 0.6714788615412663입니다. 
heat flux of calculation is 0.8190800481245077
12번째 시도에서 xt_cal은

C:\Users\tojeo\anaconda3\envs\research\lib\site-packages\pandas\core\indexing.py:845: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
C:\Users\tojeo\anaconda3\envs\research\lib\site-packages\pandas\core\indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s



heat flux of calculation is 1.1762109914756151
5번째 시도에서 xt_cal은 0.6039469690876095입니다. 
heat flux of calculation is 1.1217874785335569
6번째 시도에서 xt_cal은 0.6139469690876095입니다. 
heat flux of calculation is 1.068861970255143
7번째 시도에서 xt_cal은 0.6239469690876095입니다. 
heat flux of calculation is 1.01744334354805
8번째 시도에서 xt_cal은 0.6339469690876095입니다. 
heat flux of calculation is 0.9675385620096604
9번째 시도에서 xt_cal은 0.6439469690876095입니다. 
heat flux of calculation is 0.9191525819260946
10번째 시도에서 xt_cal은 0.6539469690876095입니다. 
heat flux of calculation is 0.8722882721701767
11번째 시도에서 xt_cal은 0.6639469690876095입니다. 
heat flux of calculation is 0.8269463480995033
12번째 시도에서 xt_cal은 0.6739469690876095입니다. 
heat flux of calculation is 0.7831253195098555
13번째 시도에서 xt_cal은 0.6839469690876095입니다. 
heat flux of calculation is 0.7408214526464664
14번째 시도에서 xt_cal은 0.6939469690876096입니다. 
heat flux of calculation is 0.7000287462169703
15번째 시도에서 xt_cal은 0.7039469690876096입니다. 
heat flux of calculation is 

heat flux of calculation is 0.8771167082278172
2번째 시도에서 xt_cal은 0.687785149455023입니다. 
heat flux of calculation is 0.8318054932242048
3번째 시도에서 xt_cal은 0.697785149455023입니다. 
heat flux of calculation is 0.7880035645417899
4번째 시도에서 xt_cal은 0.707785149455023입니다. 
heat flux of calculation is 0.7457077400880621
5번째 시도에서 xt_cal은 0.717785149455023입니다. 
heat flux of calculation is 0.7049125273381667
6번째 시도에서 xt_cal은 0.727785149455023입니다. 
heat flux of calculation is 0.6656101214160748
7번째 시도에서 xt_cal은 0.737785149455023입니다. 
heat flux of calculation is 0.6277904161241604
8번째 시도에서 xt_cal은 0.7477851494550231입니다. 
heat flux of calculation is 0.5914410276711753
9번째 시도에서 xt_cal은 0.7577851494550231입니다. 
heat flux of calculation is 0.5565473307771595
10번째 시도에서 xt_cal은 0.7677851494550231입니다. 
heat flux of calculation is 0.5230925067620862
11번째 시도에서 xt_cal은 0.7777851494550231입니다. 
heat flux of calculation is 0.4910576031539114
12번째 시도에서 xt_cal은 0.7877851494550231입니다. 
heat flux of calculation is 0.46042

heat flux of calculation is 0.6657551324452373
2번째 시도에서 xt_cal은 0.826802635832007입니다. 
heat flux of calculation is 0.6285209350851829
3번째 시도에서 xt_cal은 0.836802635832007입니다. 
heat flux of calculation is 0.5927215271701977
4번째 시도에서 xt_cal은 0.846802635832007입니다. 
heat flux of calculation is 0.5583420568932371
5번째 시도에서 xt_cal은 0.856802635832007입니다. 
heat flux of calculation is 0.5253655559822579
6번째 시도에서 xt_cal은 0.866802635832007입니다. 
heat flux of calculation is 0.4937730130906698
7번째 시도에서 xt_cal은 0.876802635832007입니다. 
heat flux of calculation is 0.4635434558488961
8번째 시도에서 xt_cal은 0.886802635832007입니다. 
heat flux of calculation is 0.4346540410093007
9번째 시도에서 xt_cal은 0.896802635832007입니다. 
heat flux of calculation is 0.4070801520676884
10번째 시도에서 xt_cal은 0.906802635832007입니다. 
heat flux of calculation is 0.38079550369992515
11번째 시도에서 xt_cal은 0.916802635832007입니다. 
heat flux of calculation is 0.355772252312355
12번째 시도에서 xt_cal은 0.9268026358320071입니다. 
heat flux of calculation is 0.331981111

...

heat flux of calculation is 1.7699925107800154
2번째 시도에서 xt_cal은 0.36926229579873315입니다. 
heat flux of calculation is 1.6940791974660887
3번째 시도에서 xt_cal은 0.37926229579873316입니다. 
heat flux of calculation is 1.620233394357986
4번째 시도에서 xt_cal은 0.38926229579873317입니다. 
heat flux of calculation is 1.5484243439927725
5번째 시도에서 xt_cal은 0.3992622957987332입니다. 
heat flux of calculation is 1.4786252545496208
6번째 시도에서 xt_cal은 0.4092622957987332입니다. 
heat flux of calculation is 1.4108126250203226
7번째 시도에서 xt_cal은 0.4192622957987332입니다. 
heat flux of calculation is 1.3449656335983557
8번째 시도에서 xt_cal은 0.4292622957987332입니다. 
heat flux of calculation is 1.28106558265415
9번째 시도에서 xt_cal은 0.4392622957987332입니다. 
heat flux of calculation is 1.219095394803076
10번째 시도에서 xt_cal은 0.4492622957987332입니다. 
heat flux of calculation is 1.1590391555093875
11번째 시도에서 xt_cal은 0.45926229579873323입니다. 
heat flux of calculation is 1.1008816984395366
12번째 시도에서 xt_cal은 0.46926229579873324입니다. 
heat flux of calculation is 

heat flux of calculation is 2.310269557696874
7번째 시도에서 xt_cal은 0.23740928911282866입니다. 
heat flux of calculation is 2.2093923161016753
8번째 시도에서 xt_cal은 0.24740928911282867입니다. 
heat flux of calculation is 2.1123179451032237
9번째 시도에서 xt_cal은 0.2574092891128287입니다. 
heat flux of calculation is 2.01881653100398
10번째 시도에서 xt_cal은 0.2674092891128287입니다. 
heat flux of calculation is 1.9286872848194165
11번째 시도에서 xt_cal은 0.2774092891128287입니다. 
heat flux of calculation is 1.8417544185499786
12번째 시도에서 xt_cal은 0.2874092891128287입니다. 
heat flux of calculation is 1.7578636605440594
13번째 시도에서 xt_cal은 0.2974092891128287입니다. 
heat flux of calculation is 1.6768792901933605
14번째 시도에서 xt_cal은 0.3074092891128287입니다. 
heat flux of calculation is 1.5986815979933628
15번째 시도에서 xt_cal은 0.31740928911282873입니다. 
heat flux of calculation is 1.523164696674422
16번째 시도에서 xt_cal은 0.32740928911282874입니다. 
heat flux of calculation is 1.4502346242532367
17번째 시도에서 xt_cal은 0.33740928911282875입니다. 
heat flux of calculatio

heat flux of calculation is 1.1625315442019009
16번째 시도에서 xt_cal은 0.38002103940469906입니다. 
heat flux of calculation is 1.1021731567184834
17번째 시도에서 xt_cal은 0.39002103940469907입니다. 
heat flux of calculation is 1.0439933635997476
18번째 시도에서 xt_cal은 0.4000210394046991입니다. 
heat flux of calculation is 0.98794591073685
19번째 시도에서 xt_cal은 0.4100210394046991입니다. 
heat flux of calculation is 0.9339874664013668
20번째 시도에서 xt_cal은 0.4200210394046991입니다. 
heat flux of calculation is 0.8820770263339212
21번째 시도에서 xt_cal은 0.4300210394046991입니다. 
heat flux of calculation is 0.8321753864482838
22번째 시도에서 xt_cal은 0.4400210394046991입니다. 
heat flux of calculation is 0.7842446766977573
23번째 시도에서 xt_cal은 0.4500210394046991입니다. 
heat flux of calculation is 0.7382479506382322
24번째 시도에서 xt_cal은 0.46002103940469913입니다. 
heat flux of calculation is 0.6941488260229486
25번째 시도에서 xt_cal은 0.47002103940469914입니다. 
heat flux of calculation is 0.6519111724107338
26번째 시도에서 xt_cal은 0.48002103940469915입니다. 
heat flux of calcu

heat flux of calculation is 0.5435827815323749
25번째 시도에서 xt_cal은 0.5073796510906223입니다. 
heat flux of calculation is 0.5080608007173529
26번째 시도에서 xt_cal은 0.5173796510906223입니다. 
heat flux of calculation is 0.4742246421222209
27번째 시도에서 xt_cal은 0.5273796510906223입니다. 
heat flux of calculation is 0.442035431557765
28번째 시도에서 xt_cal은 0.5373796510906224입니다. 
heat flux of calculation is 0.4114534442473259
29번째 시도에서 xt_cal은 0.5473796510906224입니다. 
heat flux of calculation is 0.38243806180437484
30번째 시도에서 xt_cal은 0.5573796510906224입니다. 
heat flux of calculation is 0.35494775440678883
31번째 시도에서 xt_cal은 0.5673796510906224입니다. 
heat flux of calculation is 0.32894008624002563
32번째 시도에서 xt_cal은 0.5773796510906224입니다. 
heat flux of calculation is 0.30437174229818365
33번째 시도에서 xt_cal은 0.5873796510906224입니다. 
heat flux of calculation is 0.28119857463813686
34번째 시도에서 xt_cal은 0.5973796510906224입니다. 
heat flux of calculation is 0.2593756661818289
35번째 시도에서 xt_cal은 0.6073796510906224입니다. 
heat flux of calc

NameError: name 'db_engine' is not defined

In [20]:
# 데이터를 PostgreSQL로 저장하기
"""
sql.write_sql(val_chf_tb, 'val_res_js_tb',db_engine)
sql.write_sql(val_chf_err_tb, 'val_res_js_err_tb', db_engine)
"""
val_chf_tb.to_excel('val_chf_tb.xlsx', header=True)
val_chf_tb.to_excel('val_res_' + 'model_' + str(m_idx) +'_tb.xlsx', header=True)